# [Triangular, Pentagonal, and Hexagonal](https://projecteuler.net/problem=45)

[All hexagonal numbers are triangular numbers](https://en.wikipedia.org/wiki/Polygonal_number). Therefore this problem reduces to finding numbers that are both pentagonal and hexagonal.

One way to frame this problem is that we are finding integer solutions to
$$\frac{x(3x-1)}{2} = y(2y-1)$$
In other words, we are solving a [Diophantine equation](https://en.wikipedia.org/wiki/Diophantine_equation), which is no easy task, in general. Fortunately, there are methods to tackle equations of this form, and SageMath knows them.

In [1]:
var('x,y')

P(n) = n * (3*n - 1) / 2
H(n) = n * (2*n - 1)

params = solve_diophantine(P(x) == H(y))

Here, `params` ends up being a whole bunch of ugly parameterizations in $t$ for $x$ and $y$ satisfying $P(x) = H(y)$. Here's one, just as an example:

In [2]:
params[0]

(-1/12*(2107560*sqrt(3) + 3650401)^t*(153*sqrt(3) + 265) + 1/12*(-2107560*sqrt(3) + 3650401)^t*(153*sqrt(3) - 265) + 1/6,
 -1/24*sqrt(3)*((2107560*sqrt(3) + 3650401)^t*(153*sqrt(3) + 265) + (-2107560*sqrt(3) + 3650401)^t*(153*sqrt(3) - 265)) + 1/4)

We want to check all of these parameterizations, because one of them might generate the next pentagonal hexagonal number. We'll guess a small range of values to try for $t$ (which turns out to be all we need). We're also only interested in positive indices, but some of these parameterizations generate negative values, so we'll filter those out.

In [3]:
pent_hexes = dict()
for m, n in params:
    for t in range(-5, 5):
        u, v = m(t=t), n(t=t)
        if u <= 0 or v <= 0:
            continue
            
        pent_hexes[(u, v)] = P(u).simplify_full()

sorted(pent_hexes.values())

[1,
 40755,
 1533776805,
 57722156241751,
 2172315626468283465,
 81752926228785223683195,
 3076689623521787481625080301,
 115788137209866023854693048367775,
 4357570752679408318225730700647767185,
 163992817590548715438241125333485021875651,
 6171705692845139604123358192574644612620485685,
 232265971880541166271029746781113050017874336396775,
 8741097579580580558598793886237050331798038163335747801,
 328962466077669596861765842843615405405774318221103196349195,
 12380173439625920028715115170977828280803860360134959528069859965]

This shows the next number in the sequence as 1533776805. (This number also shows up rather quickly with a few web searches about the pentagonal hexagonal numbers, but isn't it more satisfying to compute it yourself?)

Of course, there's a lot of interesting math we're glossing over by having SageMath solve the hardest part, so let's look at how we find Diophantine solutions.

## Transformation to Pell equation
It's convenient to rearrange our equation as
$$3x^2 - x - 4y^2 + 2y = 0$$
Then, by [completing the square](https://en.wikipedia.org/wiki/Completing_the_square) on both $x$ and $y$, we can transform this to
$$(6x-1)^2 - 3(4y-1)^2 = -2$$
If we make the substitutions $X = 6x - 1$ and $Y = 4y - 1$,
$$X^2 - 3Y^2 = -2$$
then we have a generalized [Pell equation](https://en.wikipedia.org/wiki/Pell%27s_equation), which is a special category of Diophantine equations that has known solution methods.

It's important to note the implications of making these substitutions. If we think of $X$ and $Y$ as functions of $x$ and $y$, respectively, then they are [injective](https://en.wikipedia.org/wiki/Injective_function). This means that every distinct solution to our original equation maps to a distinct solution to our Pell equation, as well, so we will not "lose" any solutions by making these substitutions. However, these functions are not [surjective](https://en.wikipedia.org/wiki/Surjective_function), since some integers can not be expressed as $6x-1$ or $4y-1$ with integer $x,y$. This means a solution to our general Pell equation does not necessarily correspond to a solution to our original equation. For example, $X=3691, Y=2131$ is a solution for $X^2 - 3Y^2 = -2$, but these values correspond to $x = \frac{1846}{3}, y=533$, which are not solutions to our original equation since they aren't both integers.

The main takeaway from this should be that when we find the solutions to $X^2 - 3Y^2 = -2$, we should check that they actually correspond to integer solutions to $3x^2 - x - 4y^2 + 2y = 0$, as some will be extraneous.

## But first, we need to talk about algebraic number theory
[And if you thought my other tangents were complicated...](https://www.youtube.com/watch?v=kpk2tdsPh0A)

We could jump right in from here with the methods to solve Pell equations, but to understand *why* these methods work, it's helpful to establish a few facts.

Consider that the equation $x^2 - dy^2 = n$ can be factored into
$$\left(x + y\sqrt{d}\right)\left(x - y\sqrt{d}\right) = n$$
Also recall that we are looking for integer values for $x$ and $y$ when solving Pell equations. Numbers of the form $x + y\sqrt{d}$ where $x$ and $y$ are integers (and $d$ is a non-square integer) are [quadratic integers](https://en.wikipedia.org/wiki/Quadratic_integer) (there are other quadratic integers, too, but they have non-integer $x$ and $y$, so they don't correspond to solutions to Pell equations).

Numbers of the form $x + y\sqrt{d}$ where $x,y$ are rational (instead of just integers) form a [quadratic field](https://en.wikipedia.org/wiki/Quadratic_field), denoted $\mathbb{Q}\left(\sqrt{d}\right)$.

The *norm* of a quadratic integer $x + y\sqrt{d}$ is given by $x^2 - dy^2$. Therefore, in the language of [algebraic number theory](https://en.wikipedia.org/wiki/Algebraic_number_theory), finding integer solutions to $x^2 - dy^2 = n$ can be rephrased as finding quadratic integers in $\mathbb{Q}\left(\sqrt{d}\right)$ with norm $n$. Because of this, a solution $(x, y)$ to a Pell equation is sometimes written as $x + y\sqrt{d}$.

Furthermore, let $a = x_1 + y_1\sqrt{d}$ and let $b = x_2 + y_2\sqrt{d}$. Through some tedious algebra, you can show that the norm of $ab$ is equal to the product of the norm of $a$ and the norm of $b$, i.e. the norm is [completely multiplicative](https://en.wikipedia.org/wiki/Completely_multiplicative_function).

In [4]:
var('x1,y1,x2,y2,d')

a = x1 + y1*sqrt(d)
b = x2 + y2*sqrt(d)

x = x1*x2 + y1*y2*d
y = x1*y2 + x2*y1

assert a * b == x + y*sqrt(d)

a_norm = x1^2 - d*y1^2
b_norm = x2^2 - d*y2^2

ab_norm = x^2 - d*y^2

assert a_norm * b_norm == ab_norm

Finally, note that a quadratic integer with a norm of 1 or -1 is called a *unit*. [Dirichlet's unit theorem](https://en.wikipedia.org/wiki/Dirichlet%27s_unit_theorem) leads to a powerful result about units of real quadratic integers: there exists a [fundamental unit](https://en.wikipedia.org/wiki/Fundamental_unit_(number_theory)) that generates all other units. In other words, there exists a unit $x + y\sqrt{d}$ in $\mathbb{Q}\left(\sqrt{d}\right)$ such that every other unit can be expressed as $\left(x + y\sqrt{d}\right)^k$ for some integer $k$.

As an example, we'll have SageMath compute a fundamental unit of $\mathbb{Q}\left(\sqrt{3}\right)$.

In [5]:
K = QQ[sqrt(3)]
u, *_ = K.units()
u

sqrt3 - 2

$u$ has norm 1, and as we expect, powers of $u$ also have norm 1.

In [6]:
{u^k: (u^k).norm() for k in range(2, 6)}

{-4*sqrt3 + 7: 1, 15*sqrt3 - 26: 1, -56*sqrt3 + 97: 1, 209*sqrt3 - 362: 1}

We can apply these properties of norms and units to help solve Pell equations.

## Finding solutions to the general Pell equation
There are methods for finding solutions to a general Pell equation given only the equation, such as the Lagrange-Matthews-Mollin algorithm. However, the problem statement gives us that $P_{165} = H_{143}$. Therefore $x=165, y=143$ is a solution to our original equation; this corresponds to $989 + 571\sqrt{3}$ for our general Pell equation $X^2 - 3Y^2 = -2$.

Knowing this information lets us take a shortcut: if $X + Y\sqrt{d}$ is a solution to the *general* Pell equation $x^2 - dy^2 = n$ (i.e. $X + Y\sqrt{d}$ has norm $n$), and $x_0 + y_0\sqrt{d}$ is a solution to the *standard* Pell equation $x^2 - dy^2 = 1$ (i.e. $x_0 + y_0\sqrt{d}$ has norm 1), then
$$\left(X + Y\sqrt{d}\right)\left(x_0 + y_0\sqrt{d}\right)$$
gives *another* solution to $x^2 - dy^2 = n$ (this follows from the norm of quadratic integers being completely multiplicative). Since we have $989 + 571\sqrt{3}$ as a solution to $x^2 - 3y^2 = -2$, we can multiply it by any unit of $\mathbb{Q}\left(\sqrt{3}\right)$ with norm 1 to get another solution. Furthermore, if we can find a *fundamental unit* $u$ of $\mathbb{Q}\left(\sqrt{3}\right)$ with norm 1, we can generate *every successive solution* to $x^2 - 3y^2 = -2$ by evaluating $\left(989 + 571\sqrt{3}\right)u^k$ for successive values of $k$.

We've now reduced the problem to finding a fundamental solution to the standard Pell equation $x^2 - 3y^2 = 1$, which we happened to already find above: $-2 + \sqrt{3}$ (see [problem 66](https://projecteuler.net/problem=66) for *even more discussion* on finding solutions to standard Pell equations).

## Solution to the original problem
We now have everything we need to solve the original problem:
* an initial solution to $x^2 - 3y^2 = -2$ ($989 + 571\sqrt{3}$)
* a fundamental solution to $x^2 - 3y^2 = 1$ ($-2 + \sqrt{3}$)

To generate more solutions to $x^2 - 3y^2 = -2$, we can just repeatedly multiply $989 + 571\sqrt{3}$ by $-2 + \sqrt{3}$. However, since we want the next largest pentagonal hexagonal number, we will instead multiply by $2 + \sqrt{3}$, which will also generate solutions.

As a reminder, for each one of these solutions $X + Y\sqrt{3}$, we'll need to check if $X = 6x-1$ and $Y = 4y-1$ for any integers $x$ and $y$. For example, $\left(989 + 571\sqrt{3}\right)\left(2 + \sqrt{3}\right) = 3691 + 2131\sqrt{3}$. As we noted above, $(3691, 2131)$ is a solution to $X^2 - 3Y^2 = -2$, but does *not* correspond to a solution to $3x^2 - x - 4y^2 + 2y = 0$.

Iterating this way, we eventually get $X=191861, Y=110771$, which corresponds to the integer solutions $x=31977, y=27693$.

In [7]:
x0, y0 = 2, 1  
X, Y = 989, 571
while True:
    X, Y = x0*X + 3*y0*Y, x0*Y + y0*X
    if (X + 1) % 6 == 0 and (Y + 1) % 4 == 0:
        x, y = (X + 1) // 6, (Y + 1) // 4
        break

(x, y)

(31977, 27693)

As expected, $P_x = H_y = 1533776805$.

In [8]:
P(x)

1533776805

## Further reading
* [Solving the Pell Equation](https://www.ams.org/notices/200202/fea-lenstra.pdf)
* [The Diophantine Equation $x^2 - Dy^2 = N, D>0$](http://www.numbertheory.org/PDFS/patz5.pdf)
* [Solving the Diophantine Equation $ax^2 + bxy + cy^2 + dx + ey + f = 0$](http://www.numbertheory.org/PDFS/general_quadratic_solution.pdf)
* [Solving the generalized Pell equation $x^2 - Dy^2 = N$](https://citeseerx.ist.psu.edu/document?repid=rep1&type=pdf&doi=5ac34a344ee346855184ff949eeaed18685b155c)
* [Solving the equation ax^2 + bxy + cy^2 + dx + ey + f = 0](https://web.archive.org/web/20160323033111/http://www.jpr2718.org/ax2p.pdf)
* [Pell's Equation, I](https://kconrad.math.uconn.edu/blurbs/ugradnumthy/pelleqn1.pdf)
* [Pell's Equation, II](https://kconrad.math.uconn.edu/blurbs/ugradnumthy/pelleqn2.pdf)

## Relevant sequences
* Hexagonal pentagonal numbers: [A046180](https://oeis.org/A046180)

#### Copyright (C) 2025 filifa

This work is licensed under the [Creative Commons Attribution-ShareAlike 4.0 International license](https://creativecommons.org/licenses/by-sa/4.0/) and the [BSD Zero Clause license](https://spdx.org/licenses/0BSD.html).